In [27]:
from spuriosity_metrics import *
from compute_feature_activations import *
from collections import OrderedDict

In [28]:
model_path = '../models/robust_resnet50.pth'
device = 'cpu'
architecture = 'resnet50'

In [29]:
l = torch.load(model_path, map_location=torch.device(device))['model']

In [12]:
l

OrderedDict([('module.normalizer.new_mean',
              tensor([[[0.4850]],
              
                      [[0.4560]],
              
                      [[0.4060]]])),
             ('module.normalizer.new_std',
              tensor([[[0.2290]],
              
                      [[0.2240]],
              
                      [[0.2250]]])),
             ('module.model.conv1.weight',
              tensor([[[[ 2.8998e-03, -8.2329e-04, -2.5784e-03,  ..., -3.1941e-03,
                         -2.4553e-04,  3.4729e-03],
                        [-2.8723e-03, -7.2638e-03, -8.0492e-03,  ..., -8.0426e-03,
                         -5.0311e-03,  2.6362e-03],
                        [ 5.7547e-03,  2.7930e-03, -1.7734e-04,  ...,  3.9307e-03,
                          1.0331e-02,  1.5862e-02],
                        ...,
                        [ 5.9958e-02,  1.0286e-01,  1.3715e-01,  ...,  1.5074e-01,
                          1.0591e-01,  5.6787e-02],
                        [-3.476

In [13]:
model = torchvision.models.get_model(architecture)

In [14]:
full_model_dict = l
model_keys = [k for k in full_model_dict if 'attacker' not in k and 'normalizer' not in k]


In [15]:
model_dict = dict({k.split('module.model.')[-1]:full_model_dict[k] for k in model_keys})
model.load_state_dict(model_dict)

<All keys matched successfully>

In [16]:
normalizer_keys = [k for k in full_model_dict if 'attacker' not in k and 'normalizer' in k]
normalizer_dict = dict({k.split('_')[-1]:full_model_dict[k] for k in normalizer_keys})
normalizer = torchvision.transforms.Normalize(mean=normalizer_dict['mean'], std=normalizer_dict['std'])
    

In [17]:
encoder = torch.nn.Sequential(
        OrderedDict([
            ('normalizer',normalizer), 
            *list(model.named_children())[:-1], 
            ('flatten', torch.nn.Flatten())
        ])
    )

In [18]:
encoder.eval()

Sequential(
  (normalizer): Normalize(mean=tensor([[[0.4850]],
  
          [[0.4560]],
  
          [[0.4060]]]), std=tensor([[[0.2290]],
  
          [[0.2240]],
  
          [[0.2250]]]))
  (conv1): Conv2d(3, 64, kernel_size=(7, 7), stride=(2, 2), padding=(3, 3), bias=False)
  (bn1): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (relu): ReLU(inplace=True)
  (maxpool): MaxPool2d(kernel_size=3, stride=2, padding=1, dilation=1, ceil_mode=False)
  (layer1): Sequential(
    (0): Bottleneck(
      (conv1): Conv2d(64, 64, kernel_size=(1, 1), stride=(1, 1), bias=False)
      (bn1): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (conv2): Conv2d(64, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
      (bn2): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (conv3): Conv2d(64, 256, kernel_size=(1, 1), stride=(1, 1), bias=False)
      (bn3): BatchNorm2d(256, eps=1e

In [19]:
encoder.eval().to(device)

Sequential(
  (normalizer): Normalize(mean=tensor([[[0.4850]],
  
          [[0.4560]],
  
          [[0.4060]]]), std=tensor([[[0.2290]],
  
          [[0.2240]],
  
          [[0.2250]]]))
  (conv1): Conv2d(3, 64, kernel_size=(7, 7), stride=(2, 2), padding=(3, 3), bias=False)
  (bn1): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (relu): ReLU(inplace=True)
  (maxpool): MaxPool2d(kernel_size=3, stride=2, padding=1, dilation=1, ceil_mode=False)
  (layer1): Sequential(
    (0): Bottleneck(
      (conv1): Conv2d(64, 64, kernel_size=(1, 1), stride=(1, 1), bias=False)
      (bn1): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (conv2): Conv2d(64, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
      (bn2): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (conv3): Conv2d(64, 256, kernel_size=(1, 1), stride=(1, 1), bias=False)
      (bn3): BatchNorm2d(256, eps=1e

In [20]:
model_path = '../models/robust_resnet50.pth'
device='cpu'
architecture='resnet50'

full_model_dict = torch.load(model_path, map_location=torch.device(device))['model']
model = torchvision.models.get_model(architecture)


In [21]:
full_model_dict

OrderedDict([('module.normalizer.new_mean',
              tensor([[[0.4850]],
              
                      [[0.4560]],
              
                      [[0.4060]]])),
             ('module.normalizer.new_std',
              tensor([[[0.2290]],
              
                      [[0.2240]],
              
                      [[0.2250]]])),
             ('module.model.conv1.weight',
              tensor([[[[ 2.8998e-03, -8.2329e-04, -2.5784e-03,  ..., -3.1941e-03,
                         -2.4553e-04,  3.4729e-03],
                        [-2.8723e-03, -7.2638e-03, -8.0492e-03,  ..., -8.0426e-03,
                         -5.0311e-03,  2.6362e-03],
                        [ 5.7547e-03,  2.7930e-03, -1.7734e-04,  ...,  3.9307e-03,
                          1.0331e-02,  1.5862e-02],
                        ...,
                        [ 5.9958e-02,  1.0286e-01,  1.3715e-01,  ...,  1.5074e-01,
                          1.0591e-01,  5.6787e-02],
                        [-3.476

In [22]:
model

ResNet(
  (conv1): Conv2d(3, 64, kernel_size=(7, 7), stride=(2, 2), padding=(3, 3), bias=False)
  (bn1): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (relu): ReLU(inplace=True)
  (maxpool): MaxPool2d(kernel_size=3, stride=2, padding=1, dilation=1, ceil_mode=False)
  (layer1): Sequential(
    (0): Bottleneck(
      (conv1): Conv2d(64, 64, kernel_size=(1, 1), stride=(1, 1), bias=False)
      (bn1): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (conv2): Conv2d(64, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
      (bn2): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (conv3): Conv2d(64, 256, kernel_size=(1, 1), stride=(1, 1), bias=False)
      (bn3): BatchNorm2d(256, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (relu): ReLU(inplace=True)
      (downsample): Sequential(
        (0): Conv2d(64, 256, kernel_size=(1, 1), stride=(1, 

In [23]:
# Reformat model_dict to be compatible with torchvision
model_keys = [k for k in full_model_dict if 'attacker' not in k and 'normalizer' not in k]

In [24]:


model_keys

['module.model.conv1.weight',
 'module.model.bn1.weight',
 'module.model.bn1.bias',
 'module.model.bn1.running_mean',
 'module.model.bn1.running_var',
 'module.model.bn1.num_batches_tracked',
 'module.model.layer1.0.conv1.weight',
 'module.model.layer1.0.bn1.weight',
 'module.model.layer1.0.bn1.bias',
 'module.model.layer1.0.bn1.running_mean',
 'module.model.layer1.0.bn1.running_var',
 'module.model.layer1.0.bn1.num_batches_tracked',
 'module.model.layer1.0.conv2.weight',
 'module.model.layer1.0.bn2.weight',
 'module.model.layer1.0.bn2.bias',
 'module.model.layer1.0.bn2.running_mean',
 'module.model.layer1.0.bn2.running_var',
 'module.model.layer1.0.bn2.num_batches_tracked',
 'module.model.layer1.0.conv3.weight',
 'module.model.layer1.0.bn3.weight',
 'module.model.layer1.0.bn3.bias',
 'module.model.layer1.0.bn3.running_mean',
 'module.model.layer1.0.bn3.running_var',
 'module.model.layer1.0.bn3.num_batches_tracked',
 'module.model.layer1.0.downsample.0.weight',
 'module.model.layer1.0.

In [25]:
model_dict = dict({k.split('module.model.')[-1]:full_model_dict[k] for k in model_keys})


In [26]:
model_dict

{'conv1.weight': tensor([[[[ 2.8998e-03, -8.2329e-04, -2.5784e-03,  ..., -3.1941e-03,
            -2.4553e-04,  3.4729e-03],
           [-2.8723e-03, -7.2638e-03, -8.0492e-03,  ..., -8.0426e-03,
            -5.0311e-03,  2.6362e-03],
           [ 5.7547e-03,  2.7930e-03, -1.7734e-04,  ...,  3.9307e-03,
             1.0331e-02,  1.5862e-02],
           ...,
           [ 5.9958e-02,  1.0286e-01,  1.3715e-01,  ...,  1.5074e-01,
             1.0591e-01,  5.6787e-02],
           [-3.4768e-02, -6.2510e-02, -9.3501e-02,  ..., -1.2522e-01,
            -1.1037e-01, -7.5936e-02],
           [-5.2676e-02, -9.4296e-02, -1.2052e-01,  ..., -1.2031e-01,
            -9.3363e-02, -5.7330e-02]],
 
          [[ 3.9388e-03,  7.6968e-04, -1.2439e-03,  ..., -3.0836e-03,
             3.3015e-04,  4.0289e-03],
           [-1.0184e-03, -4.5329e-03, -5.2226e-03,  ..., -6.6505e-03,
            -3.4914e-03,  4.0772e-03],
           [ 8.2185e-03,  6.2860e-03,  3.6842e-03,  ...,  6.6930e-03,
             1.3052e-02

In [30]:
model.load_state_dict(model_dict)


<All keys matched successfully>

In [31]:
model

ResNet(
  (conv1): Conv2d(3, 64, kernel_size=(7, 7), stride=(2, 2), padding=(3, 3), bias=False)
  (bn1): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (relu): ReLU(inplace=True)
  (maxpool): MaxPool2d(kernel_size=3, stride=2, padding=1, dilation=1, ceil_mode=False)
  (layer1): Sequential(
    (0): Bottleneck(
      (conv1): Conv2d(64, 64, kernel_size=(1, 1), stride=(1, 1), bias=False)
      (bn1): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (conv2): Conv2d(64, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
      (bn2): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (conv3): Conv2d(64, 256, kernel_size=(1, 1), stride=(1, 1), bias=False)
      (bn3): BatchNorm2d(256, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (relu): ReLU(inplace=True)
      (downsample): Sequential(
        (0): Conv2d(64, 256, kernel_size=(1, 1), stride=(1, 

In [37]:
model

ResNet(
  (conv1): Conv2d(3, 64, kernel_size=(7, 7), stride=(2, 2), padding=(3, 3), bias=False)
  (bn1): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (relu): ReLU(inplace=True)
  (maxpool): MaxPool2d(kernel_size=3, stride=2, padding=1, dilation=1, ceil_mode=False)
  (layer1): Sequential(
    (0): Bottleneck(
      (conv1): Conv2d(64, 64, kernel_size=(1, 1), stride=(1, 1), bias=False)
      (bn1): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (conv2): Conv2d(64, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
      (bn2): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (conv3): Conv2d(64, 256, kernel_size=(1, 1), stride=(1, 1), bias=False)
      (bn3): BatchNorm2d(256, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (relu): ReLU(inplace=True)
      (downsample): Sequential(
        (0): Conv2d(64, 256, kernel_size=(1, 1), stride=(1, 

In [39]:
from PIL import Image
import torchvision.transforms as transforms

image_path = '../sample_imagenet/train/n01494475/ILSVRC2012_val_00000293.JPEG'
image = Image.open(image_path)
preprocess = transforms.Compose([
    transforms.Resize(256),
    transforms.CenterCrop(224),
    transforms.ToTensor(),
    transforms.Normalize(mean=[0.485, 0.456, 0.406], std=[0.229, 0.224, 0.225]),
])
input_tensor = preprocess(image)

input_batch = input_tensor.unsqueeze(0)  # Add batch dimension

# Pass the input through the model
output = model(input_batch)

In [41]:
output.shape

torch.Size([1, 1000])

In [ ]:
encoder = torch.nn.Sequential(
    OrderedDict([ 
        *list(model.named_children())[:-1]
    ])
)
return encoder.eval().to(device)